## Uczenie głębokie – przetwarzanie tekstu – laboratoria
# 3. RNN

RNN - rekurencyjna sieć neuronowa \
NEP - oznaczanie jednostek nazewniczych / części mowy

IOB
- O - brak jednostki nazewniczej
- I - kontynuacja jednostki
- B - początek nowej jednostki

Typy jednostek
- LOC - lokalizacja
- PER - osoba
- ORG - organizacja

Jeśli jest to jednoznaczne to nawet na początku jednostki daje się "I" \
"B" używa się zazwyczaj przy sytuacjach w których mogło być to niejednoznaczne

## Zadanie 3

Sklonuj repozytorium https://git.wmi.amu.edu.pl/kubapok/en-ner-conll-2003

Stwórz model *sequence labelling* realizujący zadanie NER, oparty o dowolną rekurencyjną sieć neuronową (możesz wzorować się na przykładzie z zajęć).

W plikach dev-0/out.tsv oraz test-A/out.tsv umieść wyniki predykcji dla dev-0/in.tsv i test-A/in.tsv odpowiednio.
Do ewaluacji wykorzystaj narzędzie GEval (https://gitlab.com/filipg/geval):

    wget https://gonito.net/get/bin/geval
    chmod u+x geval
    ./geval --help

Liczba punktów uzyskanych za zadanie zależy od uzyskanej wartości accuracy na zbiorze `test-A` (wynik zaokrąglony w górę):

    points = math.ceil(accuracy * 7.0)

⚠️ W systemie Moodle proszę załączyć plik `test-A/out.tsv` oraz link do repozytorium z rozwiązaniem zadania.


### Podejście softmax z embeddingami na przykładzie NER

In [1]:
%pip install -v torch torchtext --index-url https://download.pytorch.org/whl/cu118
%pip install -v datasets

Using pip 23.1.2 from /usr/local/lib/python3.10/dist-packages/pip (python 3.10)
Looking in indexes: https://download.pytorch.org/whl/cu118
INFO: pip is looking at multiple versions of torch to determine which version is compatible with other requirements. This could take a while.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 839.6/839.6 MB 1.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.2/23.2 MB 64.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 875.6/875.6 kB 64.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.1/13.1 MB 101.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 728.5/728.5 MB 1.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 417.9/417.9 MB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 168.4/168.4 MB 6.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.1/58.1 MB 10.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 128.2/128.2 MB 9.0

In [2]:
from collections import Counter

import torch
from torchtext.vocab import vocab
from tqdm.notebook import tqdm
import pandas as pd
from sklearn.model_selection import train_test_split

/usr/local/lib/python3.10/dist-packages/torchtext/vocab/__init__.py:4: UserWarning: 
/!\ IMPORTANT WARNING ABOUT TORCHTEXT STATUS /!\ 
Torchtext is deprecated and the last released version will be 0.18 (this one). You can silence this warning by calling the following at the beginnign of your scripts: `import torchtext; torchtext.disable_torchtext_deprecation_warning()`
  warnings.warn(torchtext._TORCHTEXT_DEPRECATION_MSG)
/usr/local/lib/python3.10/dist-packages/torchtext/utils.py:4: UserWarning: 
/!\ IMPORTANT WARNING ABOUT TORCHTEXT STATUS /!\ 
Torchtext is deprecated and the last released version will be 0.18 (this one). You can silence this warning by calling the following at the beginnign of your scripts: `import torchtext; torchtext.disable_torchtext_deprecation_warning()`
  warnings.warn(torchtext._TORCHTEXT_DEPRECATION_MSG)


In [3]:
trainval_data = pd.read_csv("train/train.tsv", sep="\t", header=None, names=["y", "x"])
train_texts, validate_texts, train_labels, validate_labels = train_test_split(
    trainval_data["x"], trainval_data["y"], test_size=0.1, random_state=42
)
training_data = []
training_labels = []
validation_data = []
validation_labels = []

for row in train_texts:
  rowtokens = row.lower().split(" ")
  training_data.append(rowtokens)

for row in train_labels:
  rowlabels = row.split()
  training_labels.append(rowlabels)

for row in validate_texts:
  rowtokens = row.lower().split(" ")
  validation_data.append(rowtokens)

for row in validate_labels:
  rowlabels = row.split()
  validation_labels.append(rowlabels)


print(training_data[1])
print(len(training_data[1]))
print(training_labels[1])
print(len(training_labels[1]))
print(validation_data[1])
print(len(validation_data[1]))
print(validation_labels[1])
print(len(validation_labels[1]))

['cricket', '-', 'pollock', 'concludes', 'warwickshire', 'career', 'with', 'flourish', '.', '</s>', 'london', '1996-08-25', '</s>', 'south', 'african', 'fast', 'bowler', 'shaun', 'pollock', 'concluded', 'his', 'warwickshire', 'career', 'with', 'a', 'flourish', 'on', 'sunday', 'by', 'taking', 'the', 'final', 'three', 'wickets', 'during', 'the', 'county', "'s", 'sunday', 'league', 'victory', 'over', 'worcestershire', '.', '</s>', 'pollock', ',', 'who', 'returns', 'home', 'on', 'tuesday', 'for', 'an', 'ankle', 'operation', ',', 'took', 'the', 'last', 'three', 'wickets', 'in', 'nine', 'balls', 'as', 'worcestershire', 'were', 'dismissed', 'for', '154', '.', '</s>', 'after', 'an', 'hour', "'s", 'interruption', 'for', 'rain', ',', 'warwickshire', 'then', 'reached', 'an', 'adjusted', 'target', 'of', '109', 'with', '13', 'balls', 'to', 'spare', 'and', 'record', 'their', 'fifth', 'win', 'in', 'the', 'last', 'six', 'games', '.', '</s>', 'warwickshire', 'are', 'currently', 'in', 'fourth', 'positio

In [4]:
test_A_data = pd.read_csv("test-A/in.tsv", sep="\t", header=None, names=["x"])
testing_A_data = []
for (labels,data) in test_A_data.iterrows():
    rowtokens = data["x"].split(" ")
    for i in range(len(rowtokens)):
        rowtokens[i] = rowtokens[i].lower()
    testing_A_data.append(rowtokens)

print(testing_A_data[1])
print(len(testing_A_data[1]))

['rugby', 'union', '-', 'cuttitta', 'back', 'for', 'italy', 'after', 'a', 'year', '.', '</s>', 'rome', '1996-12-06', '</s>', 'italy', 'recalled', 'marcello', 'cuttitta', '</s>', 'on', 'friday', 'for', 'their', 'friendly', 'against', 'scotland', 'at', 'murrayfield', 'more', 'than', 'a', 'year', 'after', 'the', '30-year-old', 'wing', 'announced', 'he', 'was', 'retiring', 'following', 'differences', 'over', 'selection', '.', '</s>', 'cuttitta', ',', 'who', 'trainer', 'george', 'coste', 'said', 'was', 'certain', 'to', 'play', 'on', 'saturday', 'week', ',', 'was', 'named', 'in', 'a', '21-man', 'squad', 'lacking', 'only', 'two', 'of', 'the', 'team', 'beaten', '54-21', 'by', 'england', 'at', 'twickenham', 'last', 'month', '.', '</s>', 'stefano', 'bordon', 'is', 'out', 'through', 'illness', 'and', 'coste', 'said', 'he', 'had', 'dropped', 'back', 'row', 'corrado', 'covi', ',', 'who', 'had', 'been', 'recalled', 'for', 'the', 'england', 'game', 'after', 'five', 'years', 'out', 'of', 'the', 'natio

In [5]:
test_dev0_data = pd.read_csv("dev-0/in.tsv", sep="\t", header=None, names=["x"])
testing_dev0_data = []
for (labels,data) in test_dev0_data.iterrows():
    rowtokens = data["x"].split(" ")
    for i in range(len(rowtokens)):
        rowtokens[i] = rowtokens[i].lower()
    testing_dev0_data.append(rowtokens)

print(testing_dev0_data[1])

['cricket', '-', 'english', 'county', 'championship', 'scores', '.', '</s>', 'london', '1996-08-30', '</s>', 'result', 'and', 'close', 'of', 'play', 'scores', 'in', 'english', 'county', 'championship', 'matches', 'on', 'friday', ':', '</s>', 'leicester', ':', 'leicestershire', 'beat', 'somerset', 'by', 'an', 'innings', 'and', '39', 'runs', '.', '</s>', 'somerset', '83', 'and', '174', '(', 'p.', 'simmons', '4-38', ')', ',', 'leicestershire', '296', '.', '</s>', 'leicestershire', '22', 'points', ',', 'somerset', '4', '.', '</s>', 'chester-le-street', ':', 'glamorgan', '259', 'and', '207', '(', 'a.', 'dale', '69', ',', 'h.', 'morris', '69', ';', 'd.', 'blenkiron', '4-43', ')', ',', 'durham', '114', '(', 's.', 'watkin', '4-28', ')', 'and', '81-3', '.', '</s>', 'tunbridge', 'wells', ':', 'nottinghamshire', '214', '(', 'p.', 'johnson', '84', ';', 'm.', 'mccague', '4-55', ')', ',', 'kent', '108-3', '.', '</s>', 'london', '(', 'the', 'oval', ')', ':', 'warwickshire', '195', ',', 'surrey', '429

In [6]:
test_dev0_labels = pd.read_csv("dev-0/expected.tsv", sep="\t", header=None, names=["y"])
testing_dev0_labels = []
for (labels,data) in test_dev0_labels.iterrows():
    rowlabels = data["y"].split(" ")
    testing_dev0_labels.append(rowlabels)

print(testing_dev0_labels[1])

['O', 'O', 'B-MISC', 'I-MISC', 'I-MISC', 'O', 'O', 'O', 'B-LOC', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-MISC', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-LOC', 'O', 'B-ORG', 'O', 'B-ORG', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-ORG', 'O', 'O', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'O', 'B-ORG', 'O', 'O', 'O', 'B-ORG', 'O', 'O', 'O', 'B-ORG', 'O', 'O', 'O', 'B-LOC', 'O', 'B-ORG', 'O', 'O', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'O', 'B-ORG', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'O', 'O', 'O', 'O', 'B-LOC', 'I-LOC', 'O', 'B-ORG', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'O', 'B-ORG', 'O', 'O', 'O', 'B-LOC', 'O', 'B-LOC', 'I-LOC', 'O', 'O', 'B-ORG', 'O', 'O', 'B-ORG', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'O', 'O', 'B-LOC', 'O', 'B-ORG', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'B-PER'

In [7]:
NER_labels = {}
i = 0
for labels in training_labels:
    for label in labels:
        if label not in NER_labels:
            NER_labels[label] = i
            i += 1

NER_labels_reverse = {v: k for k, v in NER_labels.items()}
print(NER_labels)
print(NER_labels_reverse)

{'O': 0, 'B-MISC': 1, 'B-LOC': 2, 'B-ORG': 3, 'I-ORG': 4, 'B-PER': 5, 'I-MISC': 6, 'I-PER': 7, 'I-LOC': 8}
{0: 'O', 1: 'B-MISC', 2: 'B-LOC', 3: 'B-ORG', 4: 'I-ORG', 5: 'B-PER', 6: 'I-MISC', 7: 'I-PER', 8: 'I-LOC'}


Poniżej funkcja, która tworzy słownik (https://pytorch.org/text/stable/vocab.html).

Parametr `special` określa symbole specjalne:
* `<unk>` – nieznany token
* `<pad>` – wypełnienie
* `<bos>` – początek zdania
* `<eos>` – koniec zdania

In [8]:
def build_vocab(dataset):
    counter = Counter()
    for document in dataset:
        counter.update(document)
    return vocab(counter, specials=["<unk>", "<pad>", "<bos>", "<eos>"])

In [9]:
v = build_vocab(training_data)

In [10]:
itos = v.get_itos()  # mapowanie indeksów na tokeny

In [11]:
print(itos)

['<unk>', '<pad>', '<bos>', '<eos>', 'soccer', '-', 'polish', 'first', 'division', 'results', '.', '</s>', 'warsaw', '1996-08-24', 'of', 'matches', 'on', 'saturday', ':', 'amica', 'wronki', '3', 'hutnik', 'krakow', '0', 'sokol', 'tychy', '5', 'lech', 'poznan', 'rakow', 'czestochowa', '1', 'stomil', 'olsztyn', '4', 'wisla', 'gornik', 'zabrze', 'slask', 'wroclaw', 'odra', 'wodzislaw', 'gks', 'katowice', 'polonia', 'zaglebie', 'lubin', '2', 'lks', 'lodz', 'legia', 'belchatow', 'cricket', 'pollock', 'concludes', 'warwickshire', 'career', 'with', 'flourish', 'london', '1996-08-25', 'south', 'african', 'fast', 'bowler', 'shaun', 'concluded', 'his', 'a', 'sunday', 'by', 'taking', 'the', 'final', 'three', 'wickets', 'during', 'county', "'s", 'league', 'victory', 'over', 'worcestershire', ',', 'who', 'returns', 'home', 'tuesday', 'for', 'an', 'ankle', 'operation', 'took', 'last', 'in', 'nine', 'balls', 'as', 'were', 'dismissed', '154', 'after', 'hour', 'interruption', 'rain', 'then', 'reached',

In [12]:
len(itos)  # liczba różnych tokenów w słowniku

19708

In [13]:
v["rejects"]  # indeks tokenu `on`

8200

In [14]:
v["<unk>"]  # indeks nieznanego tokenu

0

W przypadku, gdy w analizowanym tekście znajdzie się token, którego nie ma w słowniku, będzie reprezentowany przez indeks domyślny (*default index*). Ustawiamy, żeby był taki sam, jak indeks „nieznanego tokenu”:

In [15]:
v.set_default_index(v["<unk>"])

In [16]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [17]:
def data_process(dt):
    # Wektoryzacja dokumentów tekstowych.
    return [
        torch.tensor(
            [v["<bos>"]] + [v[token] for token in document] + [v["<eos>"]],
            dtype=torch.long,
            device=device
        )
        for document in dt
    ]

In [18]:
def labels_process(dt):
    # Wektoryzacja etykiet (NER)
    return [torch.tensor([0] + document + [0], dtype=torch.long, device=device) for document in dt]

In [19]:
def get_NER_tags(labels_array):
    NER_tags = []
    for labels in labels_array:
        NER_tags.append([NER_labels[label] for label in labels])
    return NER_tags

def get_labels(NER_tags_array):
    labels = []
    for NER_tags in NER_tags_array:
        labels.append([NER_labels_reverse[tag] for tag in NER_tags])
    return labels

In [20]:
training_NER_tags = get_NER_tags(training_labels)
training_labels_from_NER_tags = get_labels(training_NER_tags)
print(training_NER_tags[1])
print(training_labels[1])
print(training_labels_from_NER_tags[1])
print(len(training_NER_tags[1]))
print(len(training_labels[1]))

[0, 0, 5, 0, 3, 0, 0, 0, 0, 0, 2, 0, 0, 1, 6, 0, 0, 5, 7, 0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 0, 0, 5, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 0, 0, 0, 0, 0, 0, 3, 0, 3, 0, 3, 0, 0, 3, 0, 5, 7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
['O', 'O', 'B-PER', 'O', 'B-ORG', 'O', 'O', 'O', 'O', 'O', 'B-LOC', 'O', 'O', 'B-MISC', 'I-MISC', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'B-ORG', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-ORG', 'O', 'O', 'B-PER', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-ORG',

In [21]:
validation_NER_tags = get_NER_tags(validation_labels)
print(validation_NER_tags[1])
print(validation_labels[1])
print(len(validation_NER_tags[1]))
print(len(validation_labels[1]))

[0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 5, 7, 0, 0, 0, 0, 5, 7, 0, 5, 7, 0, 5, 7, 0, 5, 7, 0, 5, 7, 0, 5, 7, 0, 5, 7, 0, 5, 7, 0, 5, 7, 0, 5, 7, 0, 5, 7, 0, 5, 7, 0, 0]
['O', 'O', 'B-LOC', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-LOC', 'O', 'O', 'O', 'B-LOC', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-LOC', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'O', 'O', 'B-PER', 'I-PER', 'O', 'B-PER', 'I-PER', 'O', 'B-PER', 'I-PER', 'O', 'B-PER', 'I-PER', 'O', 'B-PER', 'I-PER', 'O', 'B-PER', 'I-PER', 'O', 'B-PER', 'I-PER', 'O', 'B-PER', 'I-PER', 'O', 'B-PER', 'I-PER', 'O', 'B-PER', 'I-PER', 'O', 'B-PER', 'I-PER', 'O', 'B-PER', 'I-PER', 'O', 'O']
78
78


In [22]:
testing_dev0_NER_tags = get_NER_tags(testing_dev0_labels)
print(testing_dev0_NER_tags[1])
print(testing_dev0_labels[1])
print(len(testing_dev0_NER_tags[1]))
print(len(testing_dev0_labels[1]))

[0, 0, 1, 6, 6, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 2, 0, 3, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 3, 0, 0, 0, 0, 5, 7, 0, 0, 0, 3, 0, 0, 0, 3, 0, 0, 0, 3, 0, 0, 0, 2, 0, 3, 0, 0, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 0, 3, 0, 0, 5, 7, 0, 0, 0, 0, 0, 0, 2, 8, 0, 3, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 0, 3, 0, 0, 0, 2, 0, 2, 8, 0, 0, 3, 0, 0, 3, 0, 0, 5, 7, 0, 0, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 0, 0, 2, 0, 3, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 0, 3, 0, 0, 5, 7, 0, 0, 0, 2, 0, 3, 0, 0, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 0, 3, 0, 0, 0, 0, 0, 2, 0, 3, 0, 0, 0, 0, 3, 0, 0, 5, 7, 0, 0, 5, 0, 0, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 0, 2, 0, 3, 0, 0, 0, 0, 5, 7, 0, 0, 0, 0, 0, 3, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 0, 0]
['O', 'O', 'B-MISC', 'I-MISC', 'I-MISC', 'O', 'O', 'O', 'B-LOC', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-MISC', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-LOC', 'O', 'B-ORG', 'O', 'B-ORG', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-OR

Teraz wektoryzujemy wszystkie dane:

In [23]:
train_tokens_ids = data_process(training_data)
validate_tokens_ids = data_process(validation_data)
test_A_tokens_ids = data_process(testing_A_data)
test_dev0_tokens_ids = data_process(testing_dev0_data)

In [24]:
train_labels = labels_process(training_NER_tags)
validate_labels = labels_process(validation_NER_tags)
testing_dev0_labels = labels_process(testing_dev0_NER_tags)

Przykład, jak wyglądają dane po zwektoryzowaniu:

In [25]:
print(train_tokens_ids[1])
print(training_data[1])

tensor([  2,  53,   5,  54,  55,  56,  57,  58,  59,  10,  11,  60,  61,  11,
         62,  63,  64,  65,  66,  54,  67,  68,  56,  57,  58,  69,  59,  16,
         70,  71,  72,  73,  74,  75,  76,  77,  73,  78,  79,  70,  80,  81,
         82,  83,  10,  11,  54,  84,  85,  86,  87,  16,  88,  89,  90,  91,
         92,  84,  93,  73,  94,  75,  76,  95,  96,  97,  98,  83,  99, 100,
         89, 101,  10,  11, 102,  90, 103,  79, 104,  89, 105,  84,  56, 106,
        107,  90, 108, 109,  14, 110,  58, 111,  97, 112, 113, 114, 115, 116,
        117, 118,  95,  73,  94, 119, 120,  10,  11,  56, 121, 122,  95, 123,
        124, 125, 126,  84, 127, 114, 128,  10,  11, 126, 129, 130, 131, 132,
         68, 133,  70,  80, 134,  98,  68, 135, 136, 137, 138,  73, 139,  14,
         73, 140,  84, 141,  69,  57, 142, 143, 144, 145, 146, 147,  10,  11,
        147,  79, 148,  14, 149,  89, 150, 151, 152, 153, 154, 155, 156, 131,
        157, 116, 158, 112,  73, 159,  84, 160,  68, 161, 151, 1

In [26]:
train_tokens_ids[0]

tensor([ 2,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 11,  9, 14,  6,  7,  8, 11,
         4, 15, 16, 17, 18, 11, 19, 20, 21, 22, 23, 24, 11, 25, 26, 27, 28, 29,
        21, 11, 30, 31, 32, 33, 34, 35, 11, 36, 23, 32, 37, 38, 24, 11, 39, 40,
        21, 41, 42, 32, 11, 43, 44, 32, 45, 12, 24, 11, 46, 47, 48, 49, 50, 32,
        11, 51, 12, 21, 43, 52, 48, 11,  3], device='cuda:0')

In [27]:
train_labels[0]

tensor([0, 0, 0, 1, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        3, 4, 0, 3, 4, 0, 0, 3, 4, 0, 3, 4, 0, 0, 3, 4, 0, 3, 4, 0, 0, 3, 4, 0,
        3, 4, 0, 0, 3, 4, 0, 3, 4, 0, 0, 3, 4, 0, 3, 4, 0, 0, 3, 4, 0, 3, 4, 0,
        0, 3, 4, 0, 3, 4, 0, 0, 0], device='cuda:0')

Funkcja, której użyjemy do ewaluacji:

In [28]:
def get_scores(y_true, y_pred):
    # Funkcja zwraca precyzję, pokrycie i F1
    acc_score = 0
    tp = 0
    fp = 0
    selected_items = 0
    relevant_items = 0

    for p, t in zip(y_pred, y_true):
        if p == t:
            acc_score += 1

        if p > 0 and p == t:
            tp += 1

        if p > 0:
            selected_items += 1

        if t > 0:
            relevant_items += 1

    if selected_items == 0:
        precision = 1.0
    else:
        precision = tp / selected_items

    if relevant_items == 0:
        recall = 1.0
    else:
        recall = tp / relevant_items

    if precision + recall == 0.0:
        f1 = 0.0
    else:
        f1 = 2 * precision * recall / (precision + recall)

    return precision, recall, f1

Ile mamy różnych tagów NER?

In [29]:
num_tags = max([max(x) for x in training_NER_tags]) + 1
print(num_tags)

9


Implementacja rekurencyjnej sieci neuronowej LSTM:

In [30]:
class LSTM(torch.nn.Module):

    def __init__(self):
        super(LSTM, self).__init__()
        self.emb = torch.nn.Embedding(len(v.get_itos()), 100, device=device)
        self.rec = torch.nn.LSTM(100, 256, 1, batch_first=True, device=device)
        self.fc1 = torch.nn.Linear(256, num_tags, device=device)

    def forward(self, x):
        emb = torch.relu(self.emb(x))
        lstm_output, (h_n, c_n) = self.rec(emb)
        out_weights = self.fc1(lstm_output)
        return out_weights

Stworzenie modelu:

In [31]:
lstm = LSTM()

Definicja funkcji kosztu:

In [32]:
criterion = torch.nn.CrossEntropyLoss()

Definicja optymalizatora:

In [33]:
optimizer = torch.optim.Adam(lstm.parameters())

Funkcja do ewaluacji modelu:

In [34]:
def eval_model(dataset_tokens, dataset_labels, model):
    Y_true = []
    Y_pred = []
    for i in tqdm(range(len(dataset_labels))):
        batch_tokens = dataset_tokens[i].unsqueeze(0)
        tags = list(dataset_labels[i].cpu().numpy())
        Y_true += tags

        Y_batch_pred_weights = model(batch_tokens).squeeze(0)
        Y_batch_pred = torch.argmax(Y_batch_pred_weights, 1)
        Y_pred += list(Y_batch_pred.cpu().numpy())

    return get_scores(Y_true, Y_pred)

In [35]:
def predict(dataset_tokens, model):
    Y_pred = []
    for i in tqdm(range(len(dataset_tokens))):
        batch_tokens = dataset_tokens[i].unsqueeze(0)
        Y_batch_pred_weights = model(batch_tokens).squeeze(0)
        Y_batch_pred = torch.argmax(Y_batch_pred_weights, 1)
        Y_pred.append(list(Y_batch_pred.cpu().numpy()))

    return Y_pred

Uczenie modelu:

In [36]:
NUM_EPOCHS = 30

In [37]:
for i in range(NUM_EPOCHS):
    lstm.train()
    # for i in tqdm(range(500)):
    for i in tqdm(range(len(train_labels))):
        batch_tokens = train_tokens_ids[i].unsqueeze(0)
        tags = train_labels[i].unsqueeze(1)

        predicted_tags = lstm(batch_tokens)

        optimizer.zero_grad()
        loss = criterion(predicted_tags.squeeze(0), tags.squeeze(1))

        loss.backward()
        optimizer.step()

    lstm.eval()
    print(eval_model(validate_tokens_ids, validate_labels, lstm))

  0%|          | 0/850 [00:00<?, ?it/s]

  0%|          | 0/95 [00:00<?, ?it/s]

(0.6394904458598726, 0.14437733678458442, 0.23557015485687471)


  0%|          | 0/850 [00:00<?, ?it/s]

  0%|          | 0/95 [00:00<?, ?it/s]

...

  0%|          | 0/95 [00:00<?, ?it/s]

(0.8419761737911703, 0.6911130284728214, 0.7591217817090506)


  0%|          | 0/850 [00:00<?, ?it/s]

  0%|          | 0/95 [00:00<?, ?it/s]

(0.8563810878066122, 0.6928386540120793, 0.7659777424483306)


Ewaluacja:

In [38]:
eval_model(validate_tokens_ids, validate_labels, lstm)

  0%|          | 0/95 [00:00<?, ?it/s]

(0.8563810878066122, 0.6928386540120793, 0.7659777424483306)

In [39]:
eval_model(test_dev0_tokens_ids, testing_dev0_labels, lstm)

  0%|          | 0/215 [00:00<?, ?it/s]

(0.8522872114431383, 0.7012351433232347, 0.7694176308892156)

In [40]:
test_dev0_NER_tags_predicted = predict(test_dev0_tokens_ids, lstm)
print(test_dev0_NER_tags_predicted[1])
test_dev0_labels_from_NER_tags = get_labels(test_dev0_NER_tags_predicted)
print(test_dev0_labels_from_NER_tags[1])

  0%|          | 0/215 [00:00<?, ?it/s]

[0, 0, 0, 1, 1, 6, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 6, 0, 0, 0, 0, 0, 3, 0, 3, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 3, 0, 0, 5, 0, 3, 7, 0, 0, 0, 3, 0, 0, 0, 3, 0, 0, 0, 3, 0, 0, 0, 3, 0, 3, 0, 0, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 0, 3, 0, 0, 5, 7, 0, 0, 0, 0, 0, 0, 2, 8, 0, 3, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 0, 3, 0, 0, 0, 2, 0, 0, 8, 0, 0, 3, 0, 0, 3, 0, 0, 5, 7, 0, 0, 0, 0, 5, 7, 0, 0, 5, 0, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 0, 0, 5, 0, 3, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 0, 3, 0, 0, 5, 7, 0, 0, 0, 2, 0, 3, 0, 0, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 0, 3, 0, 0, 0, 0, 0, 2, 0, 3, 0, 0, 0, 0, 3, 0, 0, 5, 7, 0, 0, 0, 0, 0, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 0, 3, 0, 3, 0, 0, 0, 0, 5, 7, 0, 0, 0, 0, 0, 3, 0, 0, 5, 7, 0, 0, 5, 7, 0, 0, 0, 0, 0]
['O', 'O', 'O', 'B-MISC', 'B-MISC', 'I-MISC', 'O', 'O', 'O', 'B-LOC', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-MISC', 'B-MISC', 'I-MISC', 'O', 'O', 'O', 'O', 'O', 'B-ORG', 'O', 'B-ORG', 'O', 'B-ORG', 'O', 'O', 'O', 'O', 'O',

In [41]:
with open("dev-0/out.tsv", "w") as f:
    for row in test_dev0_labels_from_NER_tags:
        f.write(" ".join(row[1:-1]) + "\n")

In [42]:
test_A_NER_tags_predicted = predict(test_A_tokens_ids, lstm)
print(test_A_NER_tags_predicted[1])
test_A_labels_from_NER_tags = get_labels(test_A_NER_tags_predicted)
print(test_A_labels_from_NER_tags[1])

  0%|          | 0/230 [00:00<?, ?it/s]

[0, 0, 4, 0, 3, 0, 0, 2, 0, 0, 0, 0, 0, 2, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 2, 0, 0, 0, 0, 5, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 7, 0, 0, 4, 0, 0, 0, 0, 5, 7, 0, 0, 0, 0, 5, 7, 0, 5, 7, 0, 5, 0, 0, 0, 0, 0, 5, 7, 0, 5, 0, 0, 5, 7, 0, 5, 7, 0, 5, 7, 0, 0, 5, 7, 0, 0, 0, 0, 5, 7, 0, 5, 7, 0, 5, 0, 0, 5, 7, 0, 5, 7, 0, 0, 0]
['O', 'O', 'I-ORG', 'O', 'B-ORG', 'O', 'O', 'B-LOC', 'O', 'O', 'O', 'O', 'O', 'B-LOC', 'O', 'O', 'B-LOC', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O',

In [44]:
with open("test-A/out.tsv", "w") as f:
    for row in test_A_labels_from_NER_tags:
        f.write(" ".join(row[1:-1]) + "\n")

In [45]:
print(testing_A_data[0])
print(test_A_NER_tags_predicted[0][1:-1])
print(test_A_labels_from_NER_tags[0][1:-1])

['soccer', '-', 'japan', 'get', 'lucky', 'win', ',', 'china', 'in', 'surprise', 'defeat', '.', '</s>', 'nadim', 'ladki', '</s>', 'al-ain', ',', 'united', 'arab', 'emirates', '1996-12-06', '</s>', 'japan', 'began', 'the', 'defence', 'of', 'their', 'asian', 'cup', 'title', 'with', 'a', 'lucky', '2-1', 'win', 'against', 'syria', 'in', 'a', 'group', 'c', 'championship', 'match', 'on', 'friday', '.', '</s>', 'but', 'china', 'saw', 'their', 'luck', 'desert', 'them', 'in', 'the', 'second', 'match', 'of', 'the', 'group', ',', 'crashing', 'to', 'a', 'surprise', '2-0', 'defeat', 'to', 'newcomers', 'uzbekistan', '.', '</s>', 'china', 'controlled', 'most', 'of', 'the', 'match', 'and', 'saw', 'several', 'chances', 'missed', 'until', 'the', '78th', 'minute', 'when', 'uzbek', 'striker', 'igor', 'shkvyrin', 'took', 'advantage', 'of', 'a', 'misdirected', 'defensive', 'header', 'to', 'lob', 'the', 'ball', 'over', 'the', 'advancing', 'chinese', 'keeper', 'and', 'into', 'an', 'empty', 'net', '.', '</s>', 